![Microsoft](https://raw.githubusercontent.com/microsoft/azuredatastudio/main/extensions/arc/images/microsoft-small-logo.png)
 
## Create a PostgreSQL Hyperscale - Azure Arc on an existing Azure Arc Data Controller
 
This notebook walks through the process of creating a PostgreSQL Hyperscale - Azure Arc on an existing Azure Arc Data Controller.
 
* Follow the instructions in the **Prerequisites** cell to install the tools if not already installed.
* Make sure you have the target Azure Arc Data Controller already created.

<span style="color:red"><font size="3">Please press the "Run All" button to run the notebook</font></span>

### **Check prerequisites**

In [ ]:
import sys,os,json,subprocess
def run_command():
    print("Executing: " + cmd)
    output = subprocess.run(cmd, stdout=subprocess.PIPE, stderr=subprocess.PIPE, shell=True )
    if output.returncode != 0:
        print(f'Command: {cmd} failed \n')
        print(f'\t>>>Error output: {output.stderr.decode("utf-8")}\n')
        sys.exit(f'exit code: {output.returncode}\n')
    print(f'Successfully executed: {cmd}')
    print(f'\t>>>Output: {output.stdout.decode("utf-8")}\n')
    return output.stdout.decode("utf-8")
cmd = 'azdata --version'
out = run_command()


#### **Ensure required parameters exist**

In [ ]:
# Required Values
env_var =  "AZDATA_NB_VAR_CONTROLLER_ENDPOINT" in os.environ
if env_var:
    controller_endpoint = os.environ["AZDATA_NB_VAR_CONTROLLER_ENDPOINT"]
else:
    sys.exit(f'environment variable: AZDATA_NB_VAR_CONTROLLER_ENDPOINT was not defined. Exiting\n')

env_var =  "AZDATA_NB_VAR_CONTROLLER_USERNAME" in os.environ
if env_var:
    controller_username = os.environ["AZDATA_NB_VAR_CONTROLLER_USERNAME"]
else:
    sys.exit(f'environment variable: AZDATA_NB_VAR_CONTROLLER_USERNAME was not defined. Exiting\n')

env_var =  "AZDATA_NB_VAR_CONTROLLER_PASSWORD" in os.environ
if env_var:
    controller_password = os.environ["AZDATA_NB_VAR_CONTROLLER_PASSWORD"]
else:
    sys.exit(f'environment variable: AZDATA_NB_VAR_CONTROLLER_PASSWORD was not defined. Exiting\n')

env_var =  "AZDATA_NB_VAR_POSTGRES_SERVER_GROUP_NAME" in os.environ
if env_var:
    server_group_name = os.environ["AZDATA_NB_VAR_POSTGRES_SERVER_GROUP_NAME"]
else:
    sys.exit(f'environment variable: AZDATA_NB_VAR_POSTGRES_SERVER_GROUP_NAME was not defined. Exiting\n')

env_var = "AZDATA_NB_VAR_POSTGRES_SERVER_GROUP_PASSWORD" in os.environ
if env_var:
    postgres_password = os.environ["AZDATA_NB_VAR_POSTGRES_SERVER_GROUP_PASSWORD"]
else:
    sys.exit(f'environment variable: AZDATA_NB_VAR_POSTGRES_SERVER_GROUP_PASSWORD was not defined. Exiting\n')   

env_var = "AZDATA_NB_VAR_POSTGRES_STORAGE_CLASS_DATA" in os.environ
if env_var:
    postgres_storage_class_data = os.environ["AZDATA_NB_VAR_POSTGRES_STORAGE_CLASS_DATA"]
else:
    sys.exit(f'environment variable: AZDATA_NB_VAR_POSTGRES_STORAGE_CLASS_DATA was not defined. Exiting\n')   
env_var = "AZDATA_NB_VAR_POSTGRES_STORAGE_CLASS_LOGS" in os.environ
if env_var:
    postgres_storage_class_logs = os.environ["AZDATA_NB_VAR_POSTGRES_STORAGE_CLASS_LOGS"]
else:
    sys.exit(f'environment variable: AZDATA_NB_VAR_POSTGRES_STORAGE_CLASS_LOGS was not defined. Exiting\n')   
env_var = "AZDATA_NB_VAR_POSTGRES_STORAGE_CLASS_BACKUPS" in os.environ
if env_var:
    postgres_storage_class_backups = os.environ["AZDATA_NB_VAR_POSTGRES_STORAGE_CLASS_BACKUPS"]
else:
    sys.exit(f'environment variable: AZDATA_NB_VAR_POSTGRES_STORAGE_CLASS_BACKUPS was not defined. Exiting\n')   


#### **Get optional parameters**

In [ ]:
server_group_workers = os.environ["AZDATA_NB_VAR_POSTGRES_SERVER_GROUP_WORKERS"]
server_group_port = os.environ.get("AZDATA_NB_VAR_POSTGRES_SERVER_GROUP_PORT")
server_group_engine_version = os.environ.get("AZDATA_NB_VAR_POSTGRES_SERVER_GROUP_ENGINE_VERSION")
server_group_extensions = os.environ.get("AZDATA_NB_VAR_POSTGRES_SERVER_GROUP_EXTENSIONS")
server_group_volume_size_data = os.environ.get("AZDATA_NB_VAR_POSTGRES_SERVER_GROUP_VOLUME_SIZE_DATA")
server_group_volume_size_logs = os.environ.get("AZDATA_NB_VAR_POSTGRES_SERVER_GROUP_VOLUME_SIZE_LOGS")
server_group_volume_size_backups = os.environ.get("AZDATA_NB_VAR_POSTGRES_SERVER_GROUP_VOLUME_SIZE_BACKUPS")
server_group_cores_request = os.environ.get("AZDATA_NB_VAR_POSTGRES_SERVER_GROUP_CORES_REQUEST")
server_group_cores_limit = os.environ.get("AZDATA_NB_VAR_POSTGRES_SERVER_GROUP_CORES_LIMIT")
server_group_memory_request = os.environ.get("AZDATA_NB_VAR_POSTGRES_SERVER_GROUP_MEMORY_REQUEST")
server_group_memory_limit = os.environ.get("AZDATA_NB_VAR_POSTGRES_SERVER_GROUP_MEMORY_LIMIT")

### **Creating the PostgreSQL Hyperscale - Azure Arc instance**

In [ ]:
# Login to the data controller.
#
os.environ["AZDATA_PASSWORD"] = controller_password
cmd = f'azdata login -e {controller_endpoint} -u {controller_username}'
out=run_command()

In [ ]:
print (f'Creating the PostgreSQL Hyperscale - Azure Arc instance')

workers_option = f' -w {server_group_workers}' if server_group_workers else ""
port_option = f' --port "{server_group_port}"' if server_group_port else ""
engine_version_option = f' -ev {server_group_engine_version}' if server_group_engine_version else ""
extensions_option = f' --extensions "{server_group_extensions}"' if server_group_extensions else ""
volume_size_data_option = f' -vsd {server_group_volume_size_data}Gi' if server_group_volume_size_data else ""
volume_size_logs_option = f' -vsl {server_group_volume_size_logs}Gi' if server_group_volume_size_logs else ""
volume_size_backups_option = f' -vsb {server_group_volume_size_backups}Gi' if server_group_volume_size_backups else ""
cores_request_option = f' -cr "{server_group_cores_request}"' if server_group_cores_request else ""
cores_limit_option = f' -cl "{server_group_cores_limit}"' if server_group_cores_limit else ""
memory_request_option = f' -mr "{server_group_memory_request}Gi"' if server_group_memory_request else ""
memory_limit_option = f' -ml "{server_group_memory_limit}Gi"' if server_group_memory_limit else ""

os.environ["AZDATA_PASSWORD"] = postgres_password
cmd = f'azdata arc postgres server create -n {server_group_name} -scd {postgres_storage_class_data} -scl {postgres_storage_class_logs} -scb {postgres_storage_class_backups}{workers_option}{port_option}{engine_version_option}{extensions_option}{volume_size_data_option}{volume_size_logs_option}{volume_size_backups_option}{cores_request_option}{cores_limit_option}{memory_request_option}{memory_limit_option}'
out=run_command()